# Hillslope Scale Calibration Tutorial

This notebook outlines how to perform model calibration for a selected subset of REWs. It is assumed that the selected subset is a unique sub-watershed of the full model watershed. It is furthermore assumed that channel effects are not important at the scale of the sub-watershed, so that the model can be compared to streamflow data simply by up-scaling the hillslopes output. 

Two files are required for hillslope scale calibration:

1. A shapefile corresponding to the sub-basin to be calibrated must be stored in `raw_data/watershed_poly`. 
2. Streamflow data (in units of cm/day) stored in the `calibration_data` folder. This must be gapless, daily streamflow data spanning at least the time period from `spinup_date` to `stop_date`. 

Full model calibration including channel transport is overviewed in the [Network Scale Calibration Tutorial](./network_scale_calibration.ipynb). 

In [1]:
import os
import sys
from os.path import dirname
parent_dir = dirname(dirname(os.getcwd()))
sys.path.append(os.path.join(parent_dir,'StreamflowTempModel','2_hillslope_discharge'))
sys.path.append(os.path.join(parent_dir,'StreamflowTempModel','3_channel_routing'))
import random
random.seed()
from vadoseZone import *
import glob
from groundwaterZone import *
from REW import REW
from matplotlib import pyplot as plt
import numpy as np
import seaborn as sns
import pickle
from datetime import date
import pandas as pd
import numpy as np
import geopandas as gp
import mpld3
import time
import sys
import copy
import shapely
import fiona
import folium
from ast import literal_eval as make_tuple
import hillslope_calibration
import multiprocessing as mp
%matplotlib inline

parent_dir = os.path.dirname(os.path.dirname(os.getcwd()))
sys.path.append(os.path.join(parent_dir, 'StreamflowTempModel', '1_data_preparation'))
from prep import rew_params
rew_params()

rew_config = pickle.load( open( os.path.join(parent_dir,'model_data','rew_config.p'), "rb" ) )
climate_group_forcing = pickle.load( open( os.path.join(parent_dir,'model_data','climate_group_forcing.p'), "rb" ) )
parameter_group_params = pickle.load( open( os.path.join(parent_dir,'model_data','parameter_group_params.p'), "rb" ))
model_config = pickle.load( open( os.path.join(parent_dir, 'model_data', 'model_config.p'), 'rb'))
parameter_ranges = pickle.load( open( os.path.join(parent_dir, 'model_data', 'parameter_ranges.p'), 'rb'))
start_date = model_config['start_date']
stop_date = model_config['stop_date']
spinup_date = model_config['spinup_date']
Tmax = model_config['Tmax']
dt = model_config['dt_hillslope']
resample_freq_hillslope = model_config['resample_freq_hillslope']
timestamps_hillslope = pd.date_range(start_date, stop_date, freq=resample_freq_hillslope)
t = np.linspace(0,Tmax,np.ceil(Tmax/dt)+1)

/Users/daviddralle/anaconda2/envs/py2k_model/lib/python2.7/site-packages/osgeo/gdal.py:83: DeprecationWarning: gdal.py was placed in a namespace, it is now available as osgeo.gdal
  DeprecationWarning)


## Get REWs located within calibration sub-watershed 

Here, we use the representative REW points to determine which REWs are located within the sub-watershed that we are calibrating. We want to make sure to run the model only for the REWs that are relevant for calibration. If no REWs are contained within the sub-watershed, the REW in which the sub-watershed is located will be calibrated. 

In [4]:
glob.glob(os.path.join(parent_dir,'raw_data','streams_poly','*.shp'))

['/Users/daviddralle/Dropbox/research/streamflow_temp/model_development/raw_data/streams_poly/stream_vect_2000000.shp',
 '/Users/daviddralle/Dropbox/research/streamflow_temp/model_development/raw_data/streams_poly/streams.shp',
 '/Users/daviddralle/Dropbox/research/streamflow_temp/model_development/raw_data/streams_poly/streams_clipped.shp']

In [5]:
# Note: working in Folium, ALL projections must be converted to epsg='4326'
watershed_name = 'eel'
subwatershed_name = 'elder'

#Add watershed
shapefile_path = os.path.join(parent_dir, 'raw_data','watershed_poly', watershed_name + '.shp')
basins_shape = gp.GeoDataFrame.from_file(shapefile_path).to_crs(epsg='4326')
basins_shape['coords'] = basins_shape['geometry'].apply(lambda x: x.representative_point().coords[:])
basins_shape['coords'] = [coords[0] for coords in basins_shape['coords']]
basins = basins_shape.to_crs(epsg='4326').to_json()
bounds = basins_shape.exterior.bounds

mapa = folium.Map([basins_shape['coords'][0][1], basins_shape['coords'][0][0]],
                  tiles='Stamen Terrain')

folium.GeoJson(
    basins,
    style_function=lambda feature: {
        'color' : '#00ff00',
        'fillOpacity': .05
        }
    ).add_to(mapa)


shapefile_path = os.path.join(parent_dir, 'raw_data','watershed_poly', subwatershed_name + '.shp')
basins_shape = gp.GeoDataFrame.from_file(shapefile_path).to_crs(epsg='4326')
basins_shape['coords'] = basins_shape['geometry'].apply(lambda x: x.representative_point().coords[:])
basins_shape['coords'] = [coords[0] for coords in basins_shape['coords']]
basins = basins_shape.to_crs(epsg='4326').to_json()

folium.GeoJson(
    basins,
    style_function=lambda feature: {
        'color' : '#FF0000',
        'opacity': 0.4
        }
    ).add_to(mapa)



# iframe = folium.element.IFrame(html=html, width=150, height=150)
# popup = folium.Popup(iframe, max_width=150)
# folium.Marker([basins_shape['coords'][0][1], basins_shape['coords'][0][0]], popup=popup, icon=folium.Icon(color='red',icon='info-sign')).add_to(mapa)

streams_path = glob.glob(os.path.join(parent_dir,'raw_data','streams_poly','*.shp'))[2]
streams_shape = gp.GeoDataFrame.from_file(streams_path).to_crs(epsg='4326')
streams = gp.GeoDataFrame(streams_shape['geometry'], crs=streams_shape.crs)
basins_shape = gp.GeoDataFrame.from_file(shapefile_path).to_crs(epsg='4326')
streams['RGBA'] = '#0000ff'


streams = streams.to_crs(epsg='4326').to_json()
colors = []
folium.GeoJson(
    streams,
    style_function=lambda feature: {
        'color' : feature['properties']['RGBA'],
        'weight' : 2, 
        'opacity': 1
        }
    ).add_to(mapa)


calibration_output_name = 'whole_eel.html'
# mapa.fit_bounds([[ bounds['miny'].loc[0], bounds['minx'].loc[0]], [ bounds['maxy'].loc[0], bounds['maxx'].loc[0]]])
mapa.save('/Users/daviddralle/Desktop/'+ calibration_output_name)
mapa